In [1]:
import mido
import pretty_midi
from IPython.display import Audio, display
import os
import numpy as np # pretty_midi.synthesize returns numpy array

In [2]:
def analyze_midi(midi_path):
    """
    Performs Exploratory Data Analysis (EDA) on a given MIDI file.
    Prints various statistics about the MIDI file including tracks, tempo,
    time signatures, key signatures, and lyrics.
    """
    print(f"--- Analyzing MIDI File: {os.path.basename(midi_path)} ---")
    print(f"Full Path: {os.path.abspath(midi_path)}")

    # --- Using mido for low-level details ---
    try:
        mid_mido = mido.MidiFile(midi_path)
        print("\n--- Mido Analysis ---")
        print(f"MIDI Type (0, 1, or 2): {mid_mido.type}")
        print(f"Number of Tracks: {len(mid_mido.tracks)}")
        if mid_mido.ticks_per_beat:
            print(f"Ticks per Beat (Pulses Per Quarter Note - PPQN): {mid_mido.ticks_per_beat}")
        
        track_messages_summary = []
        for i, track in enumerate(mid_mido.tracks):
            track_info = f"  Track {i} ({track.name.strip() if track.name else 'Unnamed'}): {len(track)} messages"
            note_on_count = sum(1 for msg in track if msg.type == 'note_on')
            note_off_count = sum(1 for msg in track if msg.type == 'note_off')
            track_info += f" (Note On: {note_on_count}, Note Off: {note_off_count})"
            track_messages_summary.append(track_info)
        if track_messages_summary:
            print("Track Message Counts:")
            for t_info in track_messages_summary:
                print(t_info)

    except Exception as e:
        print(f"Error loading or analyzing with mido: {e}")
        # Continue to pretty_midi analysis if mido fails for some reason
    
    # --- Using pretty_midi for higher-level info and synthesis capabilities ---
    try:
        pm = pretty_midi.PrettyMIDI(midi_path)
        print("\n--- PrettyMIDI Analysis ---")
        print(f"Estimated Total Playback Time: {pm.get_end_time():.2f} seconds")

        # Instrument/Track Details
        print(f"\nInstrument/Track Details ({len(pm.instruments)} instruments found):")
        for i, instrument in enumerate(pm.instruments):
            instrument_name = pretty_midi.program_to_instrument_name(instrument.program)
            print(f"  Track {i}: {instrument.name.strip() if instrument.name else 'Unnamed'}")
            print(f"    Program: {instrument.program} (Instrument: {instrument_name})")
            print(f"    Is Drum Track: {instrument.is_drum}")
            print(f"    Number of Notes: {len(instrument.notes)}")
            if instrument.notes:
                pitches = [note.pitch for note in instrument.notes]
                velocities = [note.velocity for note in instrument.notes]
                start_times = sorted([note.start for note in instrument.notes])
                end_times = sorted([note.end for note in instrument.notes])
                durations = [note.end - note.start for note in instrument.notes]

                print(f"    Pitch Range: {min(pitches)} ({pretty_midi.note_number_to_name(min(pitches))}) - {max(pitches)} ({pretty_midi.note_number_to_name(max(pitches))})")
                print(f"    Velocity Range: {min(velocities)} - {max(velocities)}")
                print(f"    Note Start Times (approx range): {min(start_times):.2f}s - {max(end_times):.2f}s")
                avg_duration = sum(durations)/len(durations) if durations else 0
                print(f"    Average Note Duration: {avg_duration:.3f}s")
        
        # Tempo Information
        print("\nTempo Information:")
        tempo_changes_times, tempo_changes_bpm = pm.get_tempo_changes()
        if len(tempo_changes_times) > 0:
            print(f"  Initial Estimated Tempo: {pm.estimate_tempo():.2f} BPM (globally estimated)")
            print(f"  Initial Tempo (from events): {tempo_changes_bpm[0]:.2f} BPM at {tempo_changes_times[0]:.2f}s")
            if len(tempo_changes_times) > 1:
                print("  Other tempo changes:")
                for t, bpm_val in zip(tempo_changes_times[1:], tempo_changes_bpm[1:]):
                    print(f"    At {t:.2f}s: {bpm_val:.2f} BPM")
        else:
            print("  No explicit tempo change events found by pretty_midi (may default to 120 BPM or use global estimate).")
            print(f"  Globally Estimated Tempo: {pm.estimate_tempo():.2f} BPM")


        # Time Signatures
        print("\nTime Signature Changes:")
        if pm.time_signature_changes:
            for ts in pm.time_signature_changes:
                print(f"  {ts.numerator}/{ts.denominator} at time {ts.time:.2f}s")
        else:
            print("  No explicit time signature changes found (likely defaults to 4/4).")

        # Key Signatures
        print("\nKey Signature Changes:")
        if pm.key_signature_changes:
            for ks in pm.key_signature_changes:
                print(f"  Key: {pretty_midi.key_number_to_key_name(ks.key_number)} at time {ks.time:.2f}s")
        else:
            print("  No explicit key signature changes found.")

        # Lyrics
        print("\nLyrics:")
        lyrics_found = False
        for lyric_event in pm.lyrics:
            print(f"  At {lyric_event.time:.2f}s: \"{lyric_event.text.strip()}\"")
            lyrics_found = True
        if not lyrics_found:
            print("  No lyrics found.")
        
        # Markers (Text Annotations)
        print("\nMarkers/Text Annotations:")
        annotations_found = False
        for annotation in pm.text_events: # pretty_midi calls them text_events
            print(f"  At {annotation.time:.2f}s: \"{annotation.text.strip()}\"")
            annotations_found = True
        if not annotations_found:
            print("  No markers or text annotations found.")
            
    except Exception as e:
        print(f"\nError loading or analyzing with pretty_midi: {e}")
        print("This might be due to a malformed MIDI or a missing dependency for pretty_midi.")

    print(f"\n--- End of Analysis for: {os.path.basename(midi_path)} ---")

In [3]:
midi_file_path = "../data/nesmdb_midi/train/401_ZeldaII_TheAdventureofLink_07_08TempleBGM.mid" # <--- !!! REPLACE THIS PATH !!!
if os.path.exists(midi_file_path):
    analyze_midi(midi_file_path)
else:
    print(f"ERROR: File not found at '{midi_file_path}'.")
    print("Please update the 'midi_file_path' variable in the cell above with a valid path to a MIDI file.")

--- Analyzing MIDI File: 401_ZeldaII_TheAdventureofLink_07_08TempleBGM.mid ---
Full Path: /Users/andrewyang/Library/CloudStorage/OneDrive-UCSanDiego Real/Stuff/UCSD_School_Documents/CSE/CSE153/assignment2/CSE153_TEAM_WAAK/data/nesmdb_midi/train/401_ZeldaII_TheAdventureofLink_07_08TempleBGM.mid

--- Mido Analysis ---
MIDI Type (0, 1, or 2): 1
Number of Tracks: 5
Ticks per Beat (Pulses Per Quarter Note - PPQN): 22050
Track Message Counts:
  Track 0 (Unnamed): 4 messages (Note On: 0, Note Off: 0)
  Track 1 (p1): 2373 messages (Note On: 1046, Note Off: 0)
  Track 2 (p2): 1357 messages (Note On: 378, Note Off: 0)
  Track 3 (tr): 693 messages (Note On: 690, Note Off: 0)
  Track 4 (no): 631 messages (Note On: 624, Note Off: 0)

--- PrettyMIDI Analysis ---
Estimated Total Playback Time: 92.63 seconds

Instrument/Track Details (4 instruments found):
  Track 0: p1
    Program: 80 (Instrument: Lead 1 (square))
    Is Drum Track: False
    Number of Notes: 523
    Pitch Range: 51 (D#3) - 72 (C5)
 

In [4]:
def play_midi_audio(midi_path, sample_rate=44100):
    """
    Synthesizes and plays audio from a MIDI file using pretty_midi.
    Displays an IPython.display.Audio widget.
    """
    print(f"\n--- Attempting to Play MIDI: {os.path.basename(midi_path)} ---")
    if not os.path.exists(midi_path):
        print(f"Error: MIDI file not found at {midi_path}")
        return

    try:
        pm = pretty_midi.PrettyMIDI(midi_path)
        print(f"Synthesizing audio at {sample_rate} Hz...")
        audio_data = pm.synthesize(fs=sample_rate)
        
        print("Audio synthesized. Displaying player...")
        display(Audio(data=audio_data, rate=sample_rate))
        print("If you see an audio player above, playback should be available.")
        print("Note: Playback quality depends on the synthesizer used by pretty_midi.")
        print("For higher quality, ensure FluidSynth is installed and accessible (e.g., 'sudo apt-get install fluidsynth' or 'brew install fluidsynth').")
        
    except FileNotFoundError:
         print(f"Error: The MIDI file path '{midi_path}' was not found during playback attempt.")
    except Exception as e:
        print(f"Could not play MIDI: {e}")
        print("This could be due to several reasons:")
        print("  - The MIDI file might be corrupted or in an unsupported format for pretty_midi.")
        print("  - A MIDI synthesis backend (like FluidSynth) might not be installed or configured correctly.")
        print("    pretty_midi can use an internal basic synthesizer, but FluidSynth is often better.")
        print("  - Dependent Python libraries for audio synthesis/handling (like 'soundfile' or 'scipy') might be missing if FluidSynth is not found.")


In [39]:
# midi_file_path = "../data/nesmdb_midi/all/291_ShadowoftheNinja_02_03Stage1.mid" 
# midi_file_path = '../output_from_generated_tokens.mid'
# midi_file_path = '../unigram_8bit_midi.mid'
# midi_file_path = '../markov_8bit_midi.mid'
midi_file_path = '../lstm_8bit_midi.mid'

if 'midi_file_path' in locals() and os.path.exists(midi_file_path):
    play_midi_audio(midi_file_path)
else:
    if 'midi_file_path' not in locals():
        print("ERROR: 'midi_file_path' is not defined.")
    else:
        print(f"ERROR: File not found at '{midi_file_path}' for playback.")
    print("Please ensure 'midi_file_path' is set correctly in Cell 3 or in this cell.")



--- Attempting to Play MIDI: lstm_8bit_midi.mid ---
Synthesizing audio at 44100 Hz...
Audio synthesized. Displaying player...


If you see an audio player above, playback should be available.
Note: Playback quality depends on the synthesizer used by pretty_midi.
For higher quality, ensure FluidSynth is installed and accessible (e.g., 'sudo apt-get install fluidsynth' or 'brew install fluidsynth').
